In [4]:
%%bash
export HiFST=/home/wjb31/src/hifst/hifst.mlsalt-cpu2.18Oct16/ucam-smt/ 
export PATH=$PATH:$HiFST/bin/ 
export PATH=/home/wjb31/src/openfst/openfst-1.6.3/INSTALL_DIR/bin/:$PATH

In [5]:
import sys,os,glob,subprocess
import re
sys.path.append('/home/wjb31/src/openfst//openfst-1.6.3/INSTALL_DIR/lib/python2.7/site-packages/')
sys.path.append('/home/wjb31/src/openfst//specializer-master/')
sys.path.append('/home/wjb31/MLSALT/util/python/')
import pywrapfst as fst
import specializer
import math
import string
import utilfst
DIR= '/home/wjb31/MLSALT/MLSALT8/practicals/nmt-decoding/'
MYDIR = '/home/ac2123/MLSALT8/'
from graphemeUtils import counterFcn
import smtUtils
import pickle
import time

# Assess Lattice Sizes (do not run)

In [3]:
# Count states & arcs 
# lats_paths = [DIR+'lats/hifst/lats.dev/*',DIR+'lats/hifst/lats.test/*',DIR+'lats/hifst/lats.test']
lats_paths = [DIR+'lats/hifst/lats.tune/*',DIR+'lats/hifst/lats.test/*',DIR+'lats/hifst/lats.dev/*']
out = smtUtils.countArcsStates(lats_paths)
# Print lattice sizes out
print out[0][0][0:20]
print out[1][0][0:20]
print out[2][0][0:20]

[[15405, 34933, '113.fst'], [14094, 43761, '129.fst'], [12706, 29334, '1215.fst'], [12507, 28682, '692.fst'], [12154, 32662, '1218.fst'], [11834, 26809, '688.fst'], [11751, 31615, '237.fst'], [11128, 29296, '1214.fst'], [10671, 25791, '296.fst'], [10464, 26752, '25.fst'], [10345, 23368, '314.fst'], [10197, 27828, '308.fst'], [10004, 22823, '679.fst'], [9868, 20380, '284.fst'], [9760, 20850, '254.fst'], [9558, 27944, '719.fst'], [9087, 22823, '1112.fst'], [9069, 21812, '107.fst'], [8869, 17155, '523.fst'], [8856, 22599, '88.fst']]
[[2394951, 6808366, '1123.fst'], [120687, 527716, '239.fst'], [119296, 333158, '1061.fst'], [98970, 293167, '1119.fst'], [61797, 291025, '679.fst'], [57839, 210639, '350.fst'], [55588, 167531, '285.fst'], [53105, 177334, '550.fst'], [21924, 93456, '301.fst'], [18806, 73255, '1062.fst'], [16628, 79226, '808.fst'], [15916, 52129, '320.fst'], [15863, 73751, '1083.fst'], [15659, 74401, '305.fst'], [15381, 44013, '1115.fst'], [14609, 55231, '330.fst'], [14444, 4690

# Pre-process lattices (do not run)

In [ ]:
# Preprocess lattices
# input_lats = [DIR+'lats/hifst/lats.dev/*',DIR+'lats/hifst/lats.test/*',DIR+'lats/hifst/lats.test/*',DIR+'lats/hifst/lats.test/*']
folders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.dev/',\
           '/home/ac2123/MLSALT8/Part2/lats.words.opt.test/',\
           '/home/ac2123/MLSALT8/Part2/lats.words.opt.tune/',\
           '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.dev/',\
           '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.test/',\
           '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.tune/']
lats_sets = [DIR+'lats/hifst/lats.dev/*',\
             DIR+'lats/hifst/lats.test/*',\
             DIR+'lats/hifst/lats.tune/*',\
             MYDIR+'Part1/bpe/lats_bpe.dev/*',\
             MYDIR+'Part1/bpe/lats_bpe.test/*',\
             MYDIR+'Part1/bpe/lats_bpe.tune/*']
smtUtils.processLattices(lats_sets,folders,statePruneTh=10000,pruneTh=10)

In [ ]:
# Process words tune set lattices 
folders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.tune/']
lats_sets = [DIR+'lats/hifst/lats.tune/*']
smtUtils.processLattices(lats_sets,folders,statePruneTh=10000,pruneTh=10)

# Printstrings vs counting: small scale exp

## Printstrings

### Obtain N-best paths through the lattice

In [5]:
# Obtain output from printstrings method
script = './printstrings.sh'
#ifolders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.dev/','/home/ac2123/MLSALT8/Part2/lats.words.opt.test/','/home/ac2123/MLSALT8/Part2/lats.words.opt.tune/','/home/ac2123/MLSALT8/Part2/lats.bpe.opt.dev/','/home/ac2123/MLSALT8/Part2/lats.bpe.opt.test/']
#ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.dev/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/']
ifolders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.dev/']
ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/']
nbestdepths = ['5000','10000','20000','25000']
numlattices = '100'
ifolder = ifolders[0]
times = []
for ofolder,nbestdepth in zip(ofolders,nbestdepths):
    tstart = time.time()
    print "Start time:"+" "+str(tstart)
    process = subprocess.Popen([script,ifolder,ofolder,nbestdepth,numlattices],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])
    tend=time.time()
    print "End time:"+" "+str(tend)
    times.append(tend-tstart)
print "Runtimes:"
print times

Start time: 1522845270.79
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/8.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/9.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/10.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/11.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/12.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/13.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/14.fst
/ho

/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/8.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/9.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/10.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/11.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/12.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/13.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/14.fst
/home/ac2123/ML

/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/8.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/9.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/10.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/11.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/12.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/13.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/14.fst
/home/ac2123/ML

/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/8.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/9.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/10.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/11.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/12.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/13.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/14.fst
/home/ac2123/ML

### Calculate posteriors

In [ ]:
# Obtain posteriors using printstrings method for decoding
ifolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/*']
ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.n.20000.dev/']
smoothflag = True
tstart = time.time()
ngram_dict = smtUtils.calculatePosteriors(ifolders,ofolders,smoothflag,ngramorder=4)
tend = time.time ()
print "Runtime:"+" "+str(tend-tstart)

In [8]:
# Obtain posteriors for timing analysis
ifolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.dev/*',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.10000.dev/*',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.20000.dev/*']
ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.n.5000.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.n.10000.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.n.20000.dev/']
smoothFlag = True
times = smtUtils.calculatePosteriors(ifolders,ofolders,smoothflag,ngramorder=4)
print "Runtimes:"
print times

Runtimes:
['28.7887279987', '56.378221035', '116.24048996']


In [7]:
ifolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.dev/*']
ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.n.25000.dev/']
smoothflag = True
tstart = time.time()
ngram_dict = smtUtils.calculatePosteriors(ifolders,ofolders,smoothflag,ngramorder=4)
tend = time.time ()
print "Runtime:"+" "+str(tend-tstart)

Runtime: 141.743381977


## Counting method

### Compositions

In [9]:
# Generate compositions
script ='./computePosteriors.sh'
ifolders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.dev/']
ofolders =['/home/ac2123/MLSALT8/Part2/ngram.lattice.100.raw.words.dev/']
nshortest = '10000000'
numlattices = '100'
#ifolders = ['/home/wjb31/MLSALT/MLSALT8/practicals/nmt-decoding/lats/hifst/lats.tune/']
# testlattice = '/home/wjb31/MLSALT/MLSALT8/practicals/nmt-decoding/lats/hifst/lats.test/3.fst'
for ifolder, ofolder in zip(ifolders,ofolders):
    tstart=time.time()
    process = subprocess.Popen([script,ifolder,ofolder,nshortest,numlattices],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])
    tend=time.time()
    print "Elapsed time is:"+" "+str(tend-tstart)
    


Elapsed time is: 84.3926208019


### Posterior calculation

In [6]:
ifolders =['/home/ac2123/MLSALT8/Part2/ngram.lattice.100.raw.words.dev/*',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.100.raw.words.test/*']
ofolders =['/home/ac2123/MLSALT8/Part2/ngram.lattice.100.smooth.words.dev/',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.100.smooth.words.test/']
ifolders = [ifolders[0]]
ofolders = [ofolders[0]]
tstart = time.time()
smtUtils.smoothPosteriors (ifolders,ofolders,c1=0.25,c2=0.5,clip='before')
tend = time.time()
print "Elapsed time is:"+" "+str(tend-tstart)

Elapsed time is: 1.78520107269


# Extract n-gram posteriors from N-best list

In [9]:
# Extract N-best paths from lattices
script = './printstrings.sh'
#ifolders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.dev/','/home/ac2123/MLSALT8/Part2/lats.words.opt.test/','/home/ac2123/MLSALT8/Part2/lats.words.opt.tune/','/home/ac2123/MLSALT8/Part2/lats.bpe.opt.dev/','/home/ac2123/MLSALT8/Part2/lats.bpe.opt.test/']
#ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.dev/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/']
ifolders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.dev/',\
            '/home/ac2123/MLSALT8/Part2/lats.words.opt.test/',\
            '/home/ac2123/MLSALT8/Part2/lats.words.opt.tune/',\
            '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.dev/',\
            '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.test/',\
            '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.tune/']
ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/']
ifolders = ifolders[1:-1]
ofolders = ofolders[1:-1]
times = [] 
nbestdepth = '20000'
for ifolder,ofolder in zip(ifolders,ofolders):
    print ofolder
    tstart = time.time()
    print "Start time:"+" "+str(tstart)
    process = subprocess.Popen([script,ifolder,ofolder,nbestdepth],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])
    tend=time.time()
    print "End time:"+" "+str(tend)
    times.append(tend-tstart)
print "Runtimes:"
print times

/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/
Start time: 1523095266.62
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/7.fst
/home/ac2123/MLSALT8/Part2/ngram.p

/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/8.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tun

/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/8.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/8.fst
/home/ac2123/MLSALT8/Par

/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/8.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/8.fst
/home/ac

In [ ]:
# Extract N-best paths from lattices
script = './printstrings.sh'
#ifolders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.dev/','/home/ac2123/MLSALT8/Part2/lats.words.opt.test/','/home/ac2123/MLSALT8/Part2/lats.words.opt.tune/','/home/ac2123/MLSALT8/Part2/lats.bpe.opt.dev/','/home/ac2123/MLSALT8/Part2/lats.bpe.opt.test/']
#ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.dev/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/','/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/']
ifolders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.dev/',\
            '/home/ac2123/MLSALT8/Part2/lats.words.opt.test/',\
            '/home/ac2123/MLSALT8/Part2/lats.words.opt.tune/',\
            '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.dev/',\
            '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.test/',\
            '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.tune/']
ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/']
ifolders = [ifolders[-1]]
ofolders = [ofolders[-1]]
times = [] 
nbestdepth = '20000'
for ifolder,ofolder in zip(ifolders,ofolders):
    print ofolder
    tstart = time.time()
    print "Start time:"+" "+str(tstart)
    process = subprocess.Popen([script,ifolder,ofolder,nbestdepth],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])
    tend=time.time()
    print "End time:"+" "+str(tend)
    times.append(tend-tstart)
print "Runtimes:"
print times

/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/
Start time: 1523097970.76
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/7.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpe

In [3]:
# Obtain posteriors using printstrings method for decoding
ifolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.dev/*',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.test/*',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.tune/*',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.dev/*',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.test/*',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.bpes.tune/*']
ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.test/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.tune/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.bpes.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.bpes.test/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.bpes.tune/']
# ifolders = ['/home/ac2123/MLSALT8/Part2/ngram.development/*']
# ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.posteriors.development/']
ifolders = ifolders[2:]
ofolders = ofolders[2:]
smoothflag = True
tstart = time.time()
times = smtUtils.calculatePosteriors(ifolders,ofolders,smoothflag,ngramorder=4)
tend = time.time ()
print "Runtimes:"
print times

Runtimes:
['1989.14776516', '1312.48689318', '1476.26922703', '1614.03424907']


## Experiments varying N-best list size

### Obtain n-best lists

In [5]:
# Obtain output from printstrings method from dev set for N=1000 and N=25000
script = './printstrings.sh'
ifolders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.dev/']
ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/']
nbestdepths = ['1000','25000']
ifolder = ifolders[0]
times = []
for ofolder,nbestdepth in zip(ofolders,nbestdepths):
    tstart = time.time()
    print "Start time:"+" "+str(tstart)
    process = subprocess.Popen([script,ifolder,ofolder,nbestdepth],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])
    tend=time.time()
    print "End time:"+" "+str(tend)
    times.append(tend-tstart)
print "Runtimes:"
print times

Start time: 1522935034.01
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/7.fst
/home/ac2123

/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/7.fst
/home/ac2123/MLSALT8/Part

In [3]:
# Obtain output from printstrings method from dev set for N=100 and N=5000
script = './printstrings.sh'
ifolders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.dev/']
ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/']
nbestdepths = ['100','5000']
ifolder = ifolders[0]
times = []
for ofolder,nbestdepth in zip(ofolders,nbestdepths):
    tstart = time.time()
    print "Start time:"+" "+str(tstart)
    process = subprocess.Popen([script,ifolder,ofolder,nbestdepth],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])
    tend=time.time()
    print "End time:"+" "+str(tend)
    times.append(tend-tstart)
print "Runtimes:"
print times

Start time: 1523031543.53
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/7.fst
/home/ac2123/MLSALT8/Part

/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/1.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/2.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/3.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/4.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/5.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/6.fst
/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/7.fst
/home/ac2123/MLSALT8/Part2/ngram.print

### Calculate Posteriors

In [3]:
ifolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.1000.full.dev/*',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.25000.full.dev/*']
ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.n.1000.full.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.n.25000.full.dev/']
smoothflag = True
tstart = time.time()
times = smtUtils.calculatePosteriors(ifolders,ofolders,smoothflag,ngramorder=4)
tend = time.time ()
print "Runtimes:"
print times

Runtimes:
['99.5602378845', '2003.44102216']


In [4]:
ifolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.100.full.dev/*',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.words.n.5000.full.dev/*']
ofolders = ['/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.n.100.full.dev/',\
            '/home/ac2123/MLSALT8/Part2/ngram.printstrings.posteriors.words.n.5000.full.dev/']
smoothflag = True
tstart = time.time()
times = smtUtils.calculatePosteriors(ifolders,ofolders,smoothflag,ngramorder=4)
tend = time.time ()
print "Runtimes:"
print times

Runtimes:
['15.6744031906', '390.582179785']


## Decode using printstrings posterior calculation

## Decode dev set with n=20000

In [10]:
# Setup 
dev_size = '1166'
script = './decode.sh'
set_sizes = [dev_size]
ini_files = [MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.printstrings.dev']
out_folders = [MYDIR+'Part2/LMBR/w32k/printstrings/tfnmt.transformer.dev']
num_jobs = ['40' for i in range(len(ini_files))]
# Run the jobs 
for num_job,set_size,out_folder,ini_file in zip(num_jobs,set_sizes,out_folders,ini_files):
    process = subprocess.Popen([script,num_job,set_size,out_folder,ini_file],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

Submit jobs to grid..
Your job-array 727259.1-40:1 ("sgnmt-worker") has been submitted
qstat:
job-ID  prior   name       user         state submit/start at     queue                          slots ja-task-ID 
-----------------------------------------------------------------------------------------------------------------
 727259 0.00000 sgnmt-work ac2123       qw    04/04/2018 14:47:36                                    1 1-40:1
typical job: 29 items; largest job: 35 items



In [11]:
# Score
script = './bleu.sh'
mt_outputs = [MYDIR+'Part2/LMBR/w32k/printstrings/tfnmt.transformer.dev']
wmaps = [DIR + 'data/words/wmap.en']
references = [DIR + 'data/words/dev.en']
flags = ['']
for mt_output,wmap,reference,flag in zip(mt_outputs,wmaps,references,flags):
    process = subprocess.Popen([script,mt_output,wmap,reference,flag],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

BLEU = 18.75, 57.6/27.8/15.3/8.9 (BP=0.867, ratio=0.875, hyp_len=21274, ref_len=24309)
BLEU = 18.75, 57.6/27.8/15.3/8.9 (BP=0.867, ratio=0.875, hyp_len=21274, ref_len=24309)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/printstrings/tfnmt.transformer.dev/hyps.ids
65867.9



## Decode dev set for n=1000 and n=25000

In [4]:
dev_size = '1166'
script = './decode.sh'
set_sizes = [dev_size,dev_size]
ini_files = [MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.printstrings.n.1000.dev',\
             MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.printstrings.n.25000.dev']
out_folders = [MYDIR+'Part2/LMBR/w32k/printstrings.n.1000/tfnmt.transformer.dev',\
               MYDIR+'Part2/LMBR/w32k/printstrings.n.25000/tfnmt.transformer.dev']
num_jobs = ['40' for i in range(len(ini_files))]
# Run the jobs 
for num_job,set_size,out_folder,ini_file in zip(num_jobs,set_sizes,out_folders,ini_files):
    process = subprocess.Popen([script,num_job,set_size,out_folder,ini_file],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

Submit jobs to grid..
Your job-array 727292.1-40:1 ("sgnmt-worker") has been submitted
qstat:
job-ID  prior   name       user         state submit/start at     queue                          slots ja-task-ID 
-----------------------------------------------------------------------------------------------------------------
 727292 0.00000 sgnmt-work ac2123       qw    04/05/2018 15:50:23                                    1 1-40:1
typical job: 29 items; largest job: 35 items

Submit jobs to grid..
Your job-array 727293.1-40:1 ("sgnmt-worker") has been submitted
qstat:
job-ID  prior   name       user         state submit/start at     queue                          slots ja-task-ID 
-----------------------------------------------------------------------------------------------------------------
 727292 0.00000 sgnmt-work ac2123       qw    04/05/2018 15:50:23                                    1 1-40:1
 727293 0.00000 sgnmt-work ac2123       qw    04/05/2018 15:50:23                       

In [3]:
# Score
script = './bleu.sh'
mt_outputs = [MYDIR + 'Part2/LMBR/w32k/printstrings.n.1000/tfnmt.transformer.dev',\
              MYDIR + 'Part2/LMBR/w32k/printstrings.n.25000/tfnmt.transformer.dev']
wmaps = [DIR + 'data/words/wmap.en',\
         DIR + 'data/words/wmap.en']
references = [DIR + 'data/words/dev.en',\
              DIR + 'data/words/dev.en']
flags = ['','']
for mt_output,wmap,reference,flag in zip(mt_outputs,wmaps,references,flags):
    process = subprocess.Popen([script,mt_output,wmap,reference,flag],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

BLEU = 18.71, 57.3/27.5/15.1/8.9 (BP=0.872, ratio=0.880, hyp_len=21383, ref_len=24309)
BLEU = 18.71, 57.3/27.5/15.1/8.9 (BP=0.872, ratio=0.880, hyp_len=21383, ref_len=24309)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/printstrings.n.1000/tfnmt.transformer.dev/hyps.ids
61507.7

BLEU = 18.69, 58.0/28.0/15.4/9.0 (BP=0.857, ratio=0.867, hyp_len=21065, ref_len=24309)
BLEU = 18.69, 58.0/28.0/15.4/9.0 (BP=0.857, ratio=0.867, hyp_len=21065, ref_len=24309)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/printstrings.n.25000/tfnmt.transformer.dev/hyps.ids
54962.7



## Decode with n=100 and n=5000

In [5]:
dev_size = '1166'
script = './decode.sh'
set_sizes = [dev_size,dev_size]
ini_files = [MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.printstrings.n.100.dev',\
             MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.printstrings.n.5000.dev']
out_folders = [MYDIR+'Part2/LMBR/w32k/printstrings.n.100/tfnmt.transformer.dev',\
               MYDIR+'Part2/LMBR/w32k/printstrings.n.5000/tfnmt.transformer.dev']
num_jobs = ['40' for i in range(len(ini_files))]
# Run the jobs 
for num_job,set_size,out_folder,ini_file in zip(num_jobs,set_sizes,out_folders,ini_files):
    process = subprocess.Popen([script,num_job,set_size,out_folder,ini_file],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

Submit jobs to grid..
Your job-array 727327.1-40:1 ("sgnmt-worker") has been submitted
qstat:
job-ID  prior   name       user         state submit/start at     queue                          slots ja-task-ID 
-----------------------------------------------------------------------------------------------------------------
 727327 0.00000 sgnmt-work ac2123       qw    04/06/2018 17:34:16                                    1 1-40:1
typical job: 29 items; largest job: 35 items

Submit jobs to grid..
Your job-array 727328.1-40:1 ("sgnmt-worker") has been submitted
qstat:
job-ID  prior   name       user         state submit/start at     queue                          slots ja-task-ID 
-----------------------------------------------------------------------------------------------------------------
 727327 0.00000 sgnmt-work ac2123       qw    04/06/2018 17:34:16                                    1 1-40:1
 727328 0.00000 sgnmt-work ac2123       qw    04/06/2018 17:34:17                       

In [3]:
# Score
script = './bleu.sh'
mt_outputs = [MYDIR + 'Part2/LMBR/w32k/printstrings.n.100/tfnmt.transformer.dev',\
              MYDIR + 'Part2/LMBR/w32k/printstrings.n.5000/tfnmt.transformer.dev']
wmaps = [DIR + 'data/words/wmap.en',\
         DIR + 'data/words/wmap.en']
references = [DIR + 'data/words/dev.en',\
              DIR + 'data/words/dev.en']
flags = ['','']
for mt_output,wmap,reference,flag in zip(mt_outputs,wmaps,references,flags):
    process = subprocess.Popen([script,mt_output,wmap,reference,flag],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

BLEU = 18.60, 57.9/27.9/15.4/9.0 (BP=0.854, ratio=0.864, hyp_len=21002, ref_len=24309)
BLEU = 18.60, 57.9/27.9/15.4/9.0 (BP=0.854, ratio=0.864, hyp_len=21002, ref_len=24309)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/printstrings.n.100/tfnmt.transformer.dev/hyps.ids
51873.9

BLEU = 18.65, 57.3/27.5/15.2/8.9 (BP=0.869, ratio=0.877, hyp_len=21322, ref_len=24309)
BLEU = 18.65, 57.3/27.5/15.2/8.9 (BP=0.869, ratio=0.877, hyp_len=21322, ref_len=24309)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/printstrings.n.5000/tfnmt.transformer.dev/hyps.ids
56639.5



# Decode all sets (apart from dev) with n=20000

In [5]:
ini_files = [MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.printstrings.tune',\
             MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.printstrings.test',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.printstrings.dev',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.printstrings.tune',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.printstrings.test']
out_folders = [MYDIR+'Part2/LMBR/w32k/printstrings/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/w32k/printstrings/tfnmt.transformer.test',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.test']
print ini_files[2:]

['/home/ac2123/MLSALT8/Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.printstrings.dev', '/home/ac2123/MLSALT8/Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.printstrings.tune', '/home/ac2123/MLSALT8/Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.printstrings.test']


In [8]:
dev_size = '1166'
test_size = '1160'
tune_size = '1235'
script = './decode.sh'
set_sizes = [tune_size,test_size,dev_size,tune_size,test_size]
ini_files = [MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.printstrings.tune',\
             MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.printstrings.test',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.printstrings.dev',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.printstrings.tune',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.printstrings.test']
out_folders = [MYDIR+'Part2/LMBR/w32k/printstrings/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/w32k/printstrings/tfnmt.transformer.test',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.test']
ini_files = ini_files[2:]
out_folders = out_folders[2:]
num_jobs = ['40' for i in range(len(ini_files))]
# Run the jobs 
for num_job,set_size,out_folder,ini_file in zip(num_jobs,set_sizes,out_folders,ini_files):
    process = subprocess.Popen([script,num_job,set_size,out_folder,ini_file],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

Submit jobs to grid..
Your job-array 727552.1-40:1 ("sgnmt-worker") has been submitted
qstat:
job-ID  prior   name       user         state submit/start at     queue                          slots ja-task-ID 
-----------------------------------------------------------------------------------------------------------------
 727552 0.00000 sgnmt-work ac2123       qw    04/09/2018 15:43:05                                    1 1-40:1
typical job: 30 items; largest job: 65 items

Submit jobs to grid..
Your job-array 727553.1-40:1 ("sgnmt-worker") has been submitted
qstat:
job-ID  prior   name       user         state submit/start at     queue                          slots ja-task-ID 
-----------------------------------------------------------------------------------------------------------------
 727552 0.00000 sgnmt-work ac2123       qw    04/09/2018 15:43:05                                    1 1-40:1
 727553 0.00000 sgnmt-work ac2123       qw    04/09/2018 15:43:05                       

In [9]:
script = './bleu.sh'
mt_outputs = [MYDIR+'Part2/LMBR/w32k/printstrings/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/w32k/printstrings/tfnmt.transformer.test',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.test']
wmaps = [ DIR + 'data/words/wmap.en',\
         DIR + 'data/words/wmap.en',\
         DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en']
references = [DIR + 'data/words/tune.en',\
              DIR + 'data/words/test.en',\
              DIR + 'data/words/dev.en',\
              DIR + 'data/words/tune.en',\
              DIR + 'data/words/test.en']
flags = ['','','eow','eow','eow']
for mt_output,wmap,reference,flag in zip(mt_outputs,wmaps,references,flags):
    process = subprocess.Popen([script,mt_output,wmap,reference,flag],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

BLEU = 17.47, 54.4/25.3/13.7/7.7 (BP=0.895, ratio=0.900, hyp_len=27738, ref_len=30822)
BLEU = 17.47, 54.4/25.3/13.7/7.7 (BP=0.895, ratio=0.900, hyp_len=27738, ref_len=30822)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/printstrings/tfnmt.transformer.tune/hyps.ids
121618

BLEU = 21.97, 58.2/30.2/18.2/12.0 (BP=0.883, ratio=0.889, hyp_len=23766, ref_len=26734)
BLEU = 21.97, 58.2/30.2/18.2/12.0 (BP=0.883, ratio=0.889, hyp_len=23766, ref_len=26734)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/printstrings/tfnmt.transformer.test/hyps.ids
114844

BLEU = 0.00, 0.1/0.0/0.0/0.0 (BP=0.005, ratio=0.156, hyp_len=3803, ref_len=24309)
BLEU = 0.00, 0.1/0.0/0.0/0.0 (BP=0.005, ratio=0.156, hyp_len=3803, ref_len=24309)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/bpe/printstrings/tfnmt.transformer.dev/hyps.ids
53680.1

BLEU = 0.00, 0.1/0.0/0.0/0.0 (BP=0.001, ratio=0.133, hyp_len=3812, ref_len=28716)
BLEU = 0.00, 0.1/0.0/0.0/0.0 (BP=0.001, ratio=0.133, hyp_len=3812, ref_len=

In [8]:
script = './bleu.sh'
mt_outputs = [MYDIR+'Part2/LMBR/w32k/printstrings/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/w32k/printstrings/tfnmt.transformer.test',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/bpe/printstrings/tfnmt.transformer.test']
wmaps = [ DIR + 'data/words/wmap.en',\
         DIR + 'data/words/wmap.en',\
         DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en']
references = [DIR + 'data/words/tune.en',\
              DIR + 'data/words/test.en',\
              DIR + 'data/words/dev.en',\
              DIR + 'data/words/tune.en',\
              DIR + 'data/words/test.en']
flags = ['','','eow','eow','eow']
for mt_output,wmap,reference,flag in zip(mt_outputs,wmaps,references,flags):
    process = subprocess.Popen([script,mt_output,wmap,reference,flag],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

BLEU = 17.47, 54.4/25.3/13.7/7.7 (BP=0.895, ratio=0.900, hyp_len=27738, ref_len=30822)
BLEU = 17.47, 54.4/25.3/13.7/7.7 (BP=0.895, ratio=0.900, hyp_len=27738, ref_len=30822)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/printstrings/tfnmt.transformer.tune/hyps.ids
121618

BLEU = 21.97, 58.2/30.2/18.2/12.0 (BP=0.883, ratio=0.889, hyp_len=23766, ref_len=26734)
BLEU = 21.97, 58.2/30.2/18.2/12.0 (BP=0.883, ratio=0.889, hyp_len=23766, ref_len=26734)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/printstrings/tfnmt.transformer.test/hyps.ids
114844

BLEU = 18.70, 58.5/28.1/15.5/9.0 (BP=0.855, ratio=0.864, hyp_len=21011, ref_len=24309)
BLEU = 18.70, 58.5/28.1/15.5/9.0 (BP=0.855, ratio=0.864, hyp_len=21011, ref_len=24309)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/bpe/printstrings/tfnmt.transformer.dev/hyps.ids
70328.6

BLEU = 16.88, 55.9/25.4/13.3/7.6 (BP=0.868, ratio=0.876, hyp_len=24978, ref_len=28521)
BLEU = 16.88, 55.9/25.4/13.3/7.6 (BP=0.868, ratio=0.876, hyp

# Extract posteriors directly from lattices

In [6]:
# Build counting transducers (words)
wmap = MYDIR+'Part2/wmap.ids.en'
counter = smtUtils.buildNgramCounter(wmap,maxngram=4)

In [5]:
# Build counting tranducers (bpes)
wmap = MYDIR+'Part2/wmap.bpe.ids.en'
counter = smtUtils.buildNgramCounter(wmap,maxngram=4)

In [6]:
# Generate compositions
script ='./computePosteriors.sh'
# ifolders = ['/home/ac2123/MLSALT8/Part2/lats.words.opt.dev/',\
#           '/home/ac2123/MLSALT8/Part2/lats.words.opt.test/',\
#           '/home/ac2123/MLSALT8/Part2/lats.words.opt.tune/',\
#           '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.dev/',\
#          '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.test/',\
#           '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.tune/']
#ofolders =['/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.words.dev/',\
#           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.words.test/',\
#           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.words.tune/',\
#           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.bpes.dev/',\
#           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.bpes.test/',\
#           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.bpes.tune/']
ifolders=[ '/home/ac2123/MLSALT8/Part2/lats.words.opt.tune/',\
           '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.dev/',\
           '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.test/',\
           '/home/ac2123/MLSALT8/Part2/lats.bpe.opt.tune/']
ofolders =['/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.words.tune/',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.bpes.dev/',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.bpes.test/',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.bpes.tune/']
ifolders = ifolders[1:] # process bpes only
ofolders = ofolders[1:] # process bpes only
nshortest = '10000000'
numlattices = '3'
#ifolders = ['/home/wjb31/MLSALT/MLSALT8/practicals/nmt-decoding/lats/hifst/lats.tune/']
# testlattice = '/home/wjb31/MLSALT/MLSALT8/practicals/nmt-decoding/lats/hifst/lats.test/3.fst'
for ifolder, ofolder in zip(ifolders,ofolders):
    process = subprocess.Popen([script,ifolder,ofolder,nshortest],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[1])

ERROR: WritePotentials: Write failed: standard output
Mon Apr  9 16:38:30 2018: main.INF:printstrings.sta.O2.bin starts!
Mon Apr  9 16:38:30 2018: main.INF:CONFIG parameters:
		+config
		+input=-
		+intersection-with-hypotheses.load
		+label-map
		+nbest=10000000
		+output=-
		+semiring=stdarc
		+weight
		+weight.precision=8

Mon Apr  9 16:38:33 2018: run.INF:Processed 1 files
Mon Apr  9 16:38:33 2018: main.INF:printstrings.sta.O2.bin finished!
Mon Apr  9 16:38:33 2018: main.INF:printstrings.sta.O2.bin starts!
Mon Apr  9 16:38:33 2018: main.INF:CONFIG parameters:
		+config
		+input=-
		+intersection-with-hypotheses.load
		+label-map
		+nbest=10000000
		+output=-
		+semiring=stdarc
		+weight
		+weight.precision=8

Mon Apr  9 16:38:34 2018: run.INF:Processed 1 files
Mon Apr  9 16:38:34 2018: main.INF:printstrings.sta.O2.bin finished!
ERROR: WritePotentials: Write failed: standard output
Mon Apr  9 16:38:34 2018: main.INF:printstrings.sta.O2.bin starts!
Mon Apr  9 16:38:34 2018: main.INF:

Mon Apr  9 17:07:36 2018: main.INF:printstrings.sta.O2.bin starts!
Mon Apr  9 17:07:36 2018: main.INF:CONFIG parameters:
		+config
		+input=-
		+intersection-with-hypotheses.load
		+label-map
		+nbest=10000000
		+output=-
		+semiring=stdarc
		+weight
		+weight.precision=8

Mon Apr  9 17:07:36 2018: run.INF:Processed 1 files
Mon Apr  9 17:07:36 2018: main.INF:printstrings.sta.O2.bin finished!
Mon Apr  9 17:07:36 2018: main.INF:printstrings.sta.O2.bin starts!
Mon Apr  9 17:07:36 2018: main.INF:CONFIG parameters:
		+config
		+input=-
		+intersection-with-hypotheses.load
		+label-map
		+nbest=10000000
		+output=-
		+semiring=stdarc
		+weight
		+weight.precision=8

Mon Apr  9 17:07:37 2018: run.INF:Processed 1 files
Mon Apr  9 17:07:37 2018: main.INF:printstrings.sta.O2.bin finished!
Mon Apr  9 17:07:37 2018: main.INF:printstrings.sta.O2.bin starts!
Mon Apr  9 17:07:37 2018: main.INF:CONFIG parameters:
		+config
		+input=-
		+intersection-with-hypotheses.load
		+label-map
		+nbest=10000000


ERROR: WritePotentials: Write failed: standard output
Mon Apr  9 17:34:44 2018: main.INF:printstrings.sta.O2.bin starts!
Mon Apr  9 17:34:44 2018: main.INF:CONFIG parameters:
		+config
		+input=-
		+intersection-with-hypotheses.load
		+label-map
		+nbest=10000000
		+output=-
		+semiring=stdarc
		+weight
		+weight.precision=8

Mon Apr  9 17:34:47 2018: run.INF:Processed 1 files
Mon Apr  9 17:34:47 2018: main.INF:printstrings.sta.O2.bin finished!
ERROR: WritePotentials: Write failed: standard output
Mon Apr  9 17:34:47 2018: main.INF:printstrings.sta.O2.bin starts!
Mon Apr  9 17:34:47 2018: main.INF:CONFIG parameters:
		+config
		+input=-
		+intersection-with-hypotheses.load
		+label-map
		+nbest=10000000
		+output=-
		+semiring=stdarc
		+weight
		+weight.precision=8

Mon Apr  9 17:34:50 2018: run.INF:Processed 1 files
Mon Apr  9 17:34:50 2018: main.INF:printstrings.sta.O2.bin finished!
Mon Apr  9 17:34:50 2018: main.INF:printstrings.sta.O2.bin starts!
Mon Apr  9 17:34:50 2018: main.INF:

In [7]:
# Process files to obtain smoothed posterior
ifolders =['/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.words.dev/*',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.words.test/*',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.words.tune/*',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.bpes.dev/*',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.bpes.test/*',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.raw.bpes.tune/*']
ofolders =['/home/ac2123/MLSALT8/Part2/ngram.lattice.smooth.words.dev/',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.smooth.words.test/',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.smooth.words.tune/',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.smooth.bpes.dev/',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.smooth.bpes.test/',\
           '/home/ac2123/MLSALT8/Part2/ngram.lattice.smooth.bpes.tune/']
ifolders = ifolders[3:] # process bpes only
ofolders = ofolders[3:] # process bpes only
smtUtils.smoothPosteriors (ifolders,ofolders,c1=0.25,c2=0.5,clip='before')

# Run Smoothed Posterior Experiments

In [10]:
dev_size = '1166'
test_size = '1160'
tune_size = '1235'
script = './decode.sh'
set_sizes = [dev_size,tune_size,test_size,dev_size,tune_size,test_size]
set_sizes = set_sizes[3:] #process bpes only
ini_files = [MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.dev',\
             MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.tune',\
             MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.ngramc.test',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.dev',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.tune',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.ngramc.test']
out_folders = [MYDIR+'Part2/LMBR/w32k/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/w32k/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/w32k/tfnmt.transformer.test',\
             MYDIR+'Part2/LMBR/bpe/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/bpe/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/bpe/tfnmt.transformer.test']
num_jobs = ['40' for i in range(len(ini_files))]
num_jobs = num_jobs[3:]
ini_files = ini_files[3:] #process bpes only
out_folders = out_folders[3:] # process bpes only
# Run the jobs 
for num_job,set_size,out_folder,ini_file in zip(num_jobs,set_sizes,out_folders,ini_files):
    process = subprocess.Popen([script,num_job,set_size,out_folder,ini_file],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

Submit jobs to grid..
Your job-array 727596.1-40:1 ("sgnmt-worker") has been submitted
qstat:
job-ID  prior   name       user         state submit/start at     queue                          slots ja-task-ID 
-----------------------------------------------------------------------------------------------------------------
 727596 0.00000 sgnmt-work ac2123       qw    04/09/2018 18:43:45                                    1 1-40:1
typical job: 29 items; largest job: 35 items

Submit jobs to grid..
Your job-array 727597.1-40:1 ("sgnmt-worker") has been submitted
qstat:
job-ID  prior   name       user         state submit/start at     queue                          slots ja-task-ID 
-----------------------------------------------------------------------------------------------------------------
 727596 0.00000 sgnmt-work ac2123       qw    04/09/2018 18:43:45                                    1 1-40:1
 727597 0.00000 sgnmt-work ac2123       qw    04/09/2018 18:43:45                       

In [12]:
# Run the next cell instead of this one to compare results
script = './bleu.sh'
mt_outputs = [MYDIR+'Part2/LMBR/w32k/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/w32k/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/w32k/tfnmt.transformer.test',\
             MYDIR+'Part2/LMBR/bpe/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/bpe/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/bpe/tfnmt.transformer.test']
wmaps = [DIR + 'data/words/wmap.en',\
         DIR + 'data/words/wmap.en',\
         DIR + 'data/words/wmap.en',\
         DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en']
references = [DIR + 'data/words/dev.en',\
              DIR + 'data/words/tune.en',\
              DIR + 'data/words/test.en',\
              DIR + 'data/words/dev.en',\
              DIR + 'data/words/tune.en',\
              DIR + 'data/words/test.en']
flags = ['','','','eow','eow','eow']
for mt_output,wmap,reference,flag in zip(mt_outputs,wmaps,references,flags):
    process = subprocess.Popen([script,mt_output,wmap,reference,flag],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

BLEU = 18.93, 57.1/27.5/15.2/8.9 (BP=0.882, ratio=0.889, hyp_len=21599, ref_len=24309)
BLEU = 18.93, 57.1/27.5/15.2/8.9 (BP=0.882, ratio=0.889, hyp_len=21599, ref_len=24309)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/tfnmt.transformer.dev/hyps.ids
87253.7

BLEU = 17.43, 55.4/25.9/13.9/7.9 (BP=0.874, ratio=0.882, hyp_len=27171, ref_len=30822)
BLEU = 17.43, 55.4/25.9/13.9/7.9 (BP=0.874, ratio=0.882, hyp_len=27171, ref_len=30822)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/tfnmt.transformer.tune/hyps.ids
105446

BLEU = 21.96, 58.7/30.6/18.5/12.1 (BP=0.872, ratio=0.880, hyp_len=23520, ref_len=26734)
BLEU = 21.96, 58.7/30.6/18.5/12.1 (BP=0.872, ratio=0.880, hyp_len=23520, ref_len=26734)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/tfnmt.transformer.test/hyps.ids
91982.3

BLEU = 18.78, 58.7/28.2/15.5/9.0 (BP=0.856, ratio=0.865, hyp_len=21034, ref_len=24309)
BLEU = 18.78, 58.7/28.2/15.5/9.0 (BP=0.856, ratio=0.865, hyp_len=21034, ref_len=24309)
Time spent

In [11]:
script = './bleu.sh'
mt_outputs = [MYDIR+'Part2/LMBR/w32k/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/w32k/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/w32k/tfnmt.transformer.test',\
             MYDIR+'Part2/LMBR/bpe/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/bpe/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/bpe/tfnmt.transformer.test']
wmaps = [DIR + 'data/words/wmap.en',\
         DIR + 'data/words/wmap.en',\
         DIR + 'data/words/wmap.en',\
         DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en']
references = [DIR + 'data/words/dev.en',\
              DIR + 'data/words/tune.en',\
              DIR + 'data/words/test.en',\
              DIR + 'data/words/dev.en',\
              DIR + 'data/words/tune.en',\
              DIR + 'data/words/test.en']
flags = ['','','','eow','eow','eow']
for mt_output,wmap,reference,flag in zip(mt_outputs,wmaps,references,flags):
    process = subprocess.Popen([script,mt_output,wmap,reference,flag],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

BLEU = 18.93, 57.1/27.5/15.2/8.9 (BP=0.882, ratio=0.889, hyp_len=21599, ref_len=24309)
BLEU = 18.93, 57.1/27.5/15.2/8.9 (BP=0.882, ratio=0.889, hyp_len=21599, ref_len=24309)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/tfnmt.transformer.dev/hyps.ids
87253.7

BLEU = 17.43, 55.4/25.9/13.9/7.9 (BP=0.874, ratio=0.882, hyp_len=27171, ref_len=30822)
BLEU = 17.43, 55.4/25.9/13.9/7.9 (BP=0.874, ratio=0.882, hyp_len=27171, ref_len=30822)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/tfnmt.transformer.tune/hyps.ids
105446

BLEU = 21.96, 58.7/30.6/18.5/12.1 (BP=0.872, ratio=0.880, hyp_len=23520, ref_len=26734)
BLEU = 21.96, 58.7/30.6/18.5/12.1 (BP=0.872, ratio=0.880, hyp_len=23520, ref_len=26734)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/w32k/tfnmt.transformer.test/hyps.ids
91982.3

BLEU = 18.78, 58.7/28.2/15.5/9.0 (BP=0.856, ratio=0.865, hyp_len=21034, ref_len=24309)
BLEU = 18.78, 58.7/28.2/15.5/9.0 (BP=0.856, ratio=0.865, hyp_len=21034, ref_len=24309)
Time spent

# Pure NMT with the Transformer

In [ ]:
dev_size = '1166'
test_size = '1160'
tune_size = '1235'
script = './decode.sh'
set_sizes = [dev_size,tune_size,test_size,dev_size,tune_size,test_size]
ini_files = [MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.dev',\
             MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.tune',\
             MYDIR+'Part2/translate_jaen_kyoto32k.w32k/ini/transformer.test',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.dev',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.tune',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.test']
out_folders = [MYDIR+'Part2/PURE_NMT/w32k/tfnmt.transformer.dev',\
             MYDIR+'Part2/PURE_NMT/w32k/tfnmt.transformer.tune',\
             MYDIR+'Part2/PURE_NMT/w32k/tfnmt.transformer.test',\
             MYDIR+'Part2/PURE_NMT/bpe/tfnmt.transformer.dev',\
             MYDIR+'Part2/PURE_NMT/bpe/tfnmt.transformer.tune',\
             MYDIR+'Part2/PURE_NMT/bpe/tfnmt.transformer.test']
num_jobs = ['40' for i in range(len(ini_files))]
# Run the jobs 
for num_job,set_size,out_folder,ini_file in zip(num_jobs,set_sizes,out_folders,ini_files):
    process = subprocess.Popen([script,num_job,set_size,out_folder,ini_file],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

In [4]:
script = './bleu.sh'
mt_outputs = [MYDIR+'Part2/PURE_NMT/w32k/tfnmt.transformer.dev',\
             MYDIR+'Part2/PURE_NMT/w32k/tfnmt.transformer.tune',\
             MYDIR+'Part2/PURE_NMT/w32k/tfnmt.transformer.test',\
             MYDIR+'Part2/PURE_NMT/bpe/tfnmt.transformer.dev',\
             MYDIR+'Part2/PURE_NMT/bpe/tfnmt.transformer.tune',\
             MYDIR+'Part2/PURE_NMT/bpe/tfnmt.transformer.test']
wmaps = [DIR + 'data/words/wmap.en',\
         DIR + 'data/words/wmap.en',\
         DIR + 'data/words/wmap.en',\
         DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en']
references = [DIR + 'data/words/dev.en',\
              DIR + 'data/words/tune.en',\
              DIR + 'data/words/test.en',\
              DIR + 'data/words/dev.en',\
              DIR + 'data/words/tune.en',\
              DIR + 'data/words/test.en']
flags = ['','','','eow','eow','eow']
for mt_output,wmap,reference,flag in zip(mt_outputs,wmaps,references,flags):
    process = subprocess.Popen([script,mt_output,wmap,reference,flag],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

BLEU = 18.35, 56.7/26.8/14.8/8.7 (BP=0.872, ratio=0.880, hyp_len=21382, ref_len=24309)
BLEU = 18.35, 56.7/26.8/14.8/8.7 (BP=0.872, ratio=0.880, hyp_len=21382, ref_len=24309)
Time spent decoding /home/ac2123/MLSALT8/Part2/PURE_NMT/w32k/tfnmt.transformer.dev/hyps.ids
58049.5

BLEU = 16.92, 55.1/25.4/13.6/7.8 (BP=0.863, ratio=0.871, hyp_len=26860, ref_len=30822)
BLEU = 16.92, 55.1/25.4/13.6/7.8 (BP=0.863, ratio=0.871, hyp_len=26860, ref_len=30822)
Time spent decoding /home/ac2123/MLSALT8/Part2/PURE_NMT/w32k/tfnmt.transformer.tune/hyps.ids
73310.1

BLEU = 21.66, 58.1/30.0/18.1/11.7 (BP=0.879, ratio=0.886, hyp_len=23675, ref_len=26734)
BLEU = 21.66, 58.1/30.0/18.1/11.7 (BP=0.879, ratio=0.886, hyp_len=23675, ref_len=26734)
Time spent decoding /home/ac2123/MLSALT8/Part2/PURE_NMT/w32k/tfnmt.transformer.test/hyps.ids
58284.8

BLEU = 17.73, 56.2/25.9/13.9/8.0 (BP=0.884, ratio=0.891, hyp_len=21650, ref_len=24309)
BLEU = 17.73, 56.2/25.9/13.9/8.0 (BP=0.884, ratio=0.891, hyp_len=21650, ref_len=2430

# Run ensamble decoding model

In [ ]:
# Command below does not work when ran via jupyter but is correct

In [20]:
%%bash
export HiFST=/home/wjb31/src/hifst/hifst.mlsalt-cpu2.18Oct16/ucam-smt/ 
export PATH=$PATH:$HiFST/bin/ 
export PATH=/home/wjb31/src/openfst/openfst-1.6.3/INSTALL_DIR/bin/:$PATH
bpe2w='/home/ac2123/MLSALT8/Part1/bpe/bpe2w.fst'
bpe2wfst='/home/ac2123/MLSALT8/Part2/bpe2w.fst'
fstcompile $bpe2w | fstarcsort > $bpe2wfst

ERROR: fstcompile: Open failed, file = /home/ac2123/MLSALT8/Part1/bpe/bpe2w.fst
ERROR: FstHeader::Read: Bad FST header: standard input


In [18]:
dev_size = '1166'
test_size = '1160'
tune_size = '1235'
script = './decode.sh'
set_sizes = [dev_size,tune_size,test_size]
ini_files = [MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.bpeXw32k.ngramc.dev',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.bpeXw32k.ngramc.tune',\
             MYDIR+'Part2/translate_jaen_kyoto32k.bpe/ini/transformer.bpeXw32k.ngramc.test']
out_folders = [MYDIR+'Part2/LMBR/bpeXw32k/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/bpeXw32k/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/bpeXw32k/tfnmt.transformer.test']
num_jobs = ['40' for i in range(len(ini_files))]
# Run the jobs 
for num_job,set_size,out_folder,ini_file in zip(num_jobs,set_sizes,out_folders,ini_files):
    process = subprocess.Popen([script,num_job,set_size,out_folder,ini_file],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

Submit jobs to grid..
Your job-array 727273.1-40:1 ("sgnmt-worker") has been submitted
qstat:
job-ID  prior   name       user         state submit/start at     queue                          slots ja-task-ID 
-----------------------------------------------------------------------------------------------------------------
 727273 0.00000 sgnmt-work ac2123       qw    04/04/2018 21:44:54                                    1 1-40:1
typical job: 29 items; largest job: 35 items

Submit jobs to grid..
Your job-array 727274.1-40:1 ("sgnmt-worker") has been submitted
qstat:
job-ID  prior   name       user         state submit/start at     queue                          slots ja-task-ID 
-----------------------------------------------------------------------------------------------------------------
 727273 0.00000 sgnmt-work ac2123       qw    04/04/2018 21:44:54                                    1 1-40:1
 727274 0.00000 sgnmt-work ac2123       qw    04/04/2018 21:44:54                       

In [4]:
script = './bleu.sh'
mt_outputs = [MYDIR+'Part2/LMBR/bpeXw32k/tfnmt.transformer.dev',\
             MYDIR+'Part2/LMBR/bpeXw32k/tfnmt.transformer.tune',\
             MYDIR+'Part2/LMBR/bpeXw32k/tfnmt.transformer.test']
wmaps = [DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en',\
         DIR + 'data/bpes/wmap.bpe.en']
references = [DIR + 'data/words/dev.en',\
              DIR + 'data/words/tune.en',\
              DIR + 'data/words/test.en']
flags = ['eow','eow','eow']
for mt_output,wmap,reference,flag in zip(mt_outputs,wmaps,references,flags):
    process = subprocess.Popen([script,mt_output,wmap,reference,flag],stdout=subprocess.PIPE,stderr=subprocess.PIPE)
    print (process.communicate()[0])

BLEU = 19.45, 59.7/29.2/16.4/9.8 (BP=0.847, ratio=0.857, hyp_len=20841, ref_len=24309)
BLEU = 19.45, 59.7/29.2/16.4/9.8 (BP=0.847, ratio=0.857, hyp_len=20841, ref_len=24309)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/bpeXw32k/tfnmt.transformer.dev/hyps.ids
481962

BLEU = 17.99, 57.7/27.4/14.8/8.5 (BP=0.852, ratio=0.862, hyp_len=26579, ref_len=30822)
BLEU = 17.99, 57.7/27.4/14.8/8.5 (BP=0.852, ratio=0.862, hyp_len=26579, ref_len=30822)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/bpeXw32k/tfnmt.transformer.tune/hyps.ids
705995

BLEU = 23.51, 61.0/32.9/20.2/13.5 (BP=0.863, ratio=0.872, hyp_len=23312, ref_len=26734)
BLEU = 23.51, 61.0/32.9/20.2/13.5 (BP=0.863, ratio=0.872, hyp_len=23312, ref_len=26734)
Time spent decoding /home/ac2123/MLSALT8/Part2/LMBR/bpeXw32k/tfnmt.transformer.test/hyps.ids
663670

